In [ ]:
from dotenv import load_dotenv
from typing import Optional
import os
import yaml
import pandas as pd
import vectorbt as vbt
import numpy as np

load_dotenv()
config_path = os.getenv('3CANDLES_CONFIG_PATH')

with open(config_path, 'r') as file:
    config = yaml.safe_load(file)
    
df_hour = pd.read_csv(config['Data_filename_hour'])
df_hour = df_hour.set_index('Time')
df_hour.index = pd.to_datetime(df_hour.index)

df_hour = df_hour.drop(columns=['Volume', 'High', 'Low'])
df_hour['Dir'] = 0

df_hour.loc[df_hour['Close'] > df_hour['Open'], 'Dir'] = 1
bull_entry_mask = ((df_hour['Dir'] == 1) & (df_hour['Dir'].shift(1) == 1) & (df_hour['Dir'].shift(2) == 1) & #short
                    (df_hour['Close'].shift(2) < df_hour['Open']))
df_hour['Bull Entry'] = bull_entry_mask
bear_entry_mask = ((df_hour['Dir'] == 0) & (df_hour['Dir'].shift(1) == 0) & (df_hour['Dir'].shift(2) == 0) & #long
                    (df_hour['Close'].shift(2) > df_hour['Open']))
df_hour['Bear Entry'] = bear_entry_mask

df_hour.loc[df_hour['Bull Entry'] == True, 'SL'] = df_hour['Close'] + ((df_hour['Close'] - df_hour['Close'].shift(2)) * (config['RR'] * config['SL'])) #short
df_hour.loc[df_hour['Bear Entry'] == True, 'SL'] = df_hour['Close'] - ((df_hour['Close'].shift(2) - df_hour['Close']) * (config['RR'] * config['SL'])) #long
df_hour.loc[df_hour['Bull Entry'] == True, 'TP'] = df_hour['Close'] - ((df_hour['Close'] - df_hour['Close'].shift(2)) * (config['RR'] * config['TP'])) #short
df_hour.loc[df_hour['Bear Entry'] == True, 'TP'] = df_hour['Close'] + ((df_hour['Close'].shift(2) - df_hour['Close']) * (config['RR'] * config['TP'])) #long

index_arr_hour = df_hour.index.to_numpy()
close_arr_hour = df_hour['Close'].to_numpy()
bull_entry_arr_hour = df_hour['Bull Entry'].to_numpy()
bear_entry_arr_hour = df_hour['Bear Entry'].to_numpy()
sl_arr_hour = df_hour['SL'].to_numpy()
tp_arr_hour = df_hour['TP'].to_numpy()
price_arr_hour = np.full(len(index_arr_hour), np.nan)
bull_entrymask_arr_hour = np.full(len(index_arr_hour), False)
bear_entrymask_arr_hour = np.full(len(index_arr_hour), False)
bull_exit_arr_hour = np.full(len(index_arr_hour), False)
bear_exit_arr_hour = np.full(len(index_arr_hour), False)

trade_direct: Optional[str] = None
cur_sl: Optional[float] = None; cur_tp: Optional[float] = None

for i in range(len(index_arr_hour)):
    if trade_direct is None:

        if bull_entry_arr_hour[i]:
            trade_direct = 'bull'
            bull_entrymask_arr_hour[i] = True
            cur_sl, cur_tp = sl_arr_hour[i], tp_arr_hour[i]
            price_arr_hour[i] = close_arr_hour[i]
        elif bear_entry_arr_hour[i]:
            trade_direct = 'bear'
            bear_entrymask_arr_hour[i] = True
            cur_sl, cur_tp = sl_arr_hour[i], tp_arr_hour[i]
            price_arr_hour[i] = close_arr_hour[i]
        else:
            continue  

    elif trade_direct == 'bull':

        if close_arr_hour[i] >= cur_sl:
            price_arr_hour[i] = cur_sl
            trade_direct, cur_sl, cur_tp = None, None, None
            bull_exit_arr_hour[i] = True
        elif close_arr_hour[i] <= cur_tp:
            price_arr_hour[i] = cur_tp
            trade_direct, cur_sl, cur_tp = None, None, None
            bull_exit_arr_hour[i] = True

    elif trade_direct == 'bear':

        if close_arr_hour[i] <= cur_sl:
            price_arr_hour[i] = cur_sl
            trade_direct, cur_sl, cur_tp = None, None, None
            bear_exit_arr_hour[i] = True
        elif close_arr_hour[i] >= cur_tp:
            price_arr_hour[i] = cur_tp
            trade_direct, cur_sl, cur_tp = None, None, None
            bear_exit_arr_hour[i] = True

pf = vbt.Portfolio.from_signals(
entries = bear_entrymask_arr_hour,
exits = bear_exit_arr_hour,
short_entries = bull_entrymask_arr_hour,
short_exits = bull_exit_arr_hour,
price = price_arr_hour,
open = df_hour["Open"],
close = df_hour["Close"],
size = config['Trade']['size'],
size_type = config['Trade']['size_type'],
fees = config['Broker']['fees'],
fixed_fees = config['Broker']['fixed_fees'],
slippage = config['Slippage'],
init_cash = config['Initial_cash'],
freq = '1h'
)

In [3]:
pf.stats()

Start                         2024-01-01 22:00:00+00:00
End                           2025-12-09 09:00:00+00:00
Period                                503 days 12:00:00
Start Value                                     50000.0
End Value                                  51546.136267
Total Return [%]                               3.092273
Benchmark Return [%]                           5.475781
Max Gross Exposure [%]                        30.148416
Total Fees Paid                                     0.0
Max Drawdown [%]                               0.659674
Max Drawdown Duration                 101 days 21:00:00
Total Trades                                       1150
Total Closed Trades                                1150
Total Open Trades                                     0
Open Trade PnL                                      0.0
Win Rate [%]                                  39.130435
Best Trade [%]                                 1.228647
Worst Trade [%]                               -0

In [4]:
pf.plot().show()

In [5]:
pf.trades.records_readable.tail(21)

Exit Trade Id  Column          Size           Entry Timestamp  \
1129           1129       0  13356.768448 2025-11-28 08:00:00+00:00   
1130           1130       0  13311.775629 2025-11-28 15:00:00+00:00   
1131           1131       0  13282.823049 2025-12-01 11:00:00+00:00   
1132           1132       0  13280.492930 2025-12-01 15:00:00+00:00   
1133           1133       0  13297.207915 2025-12-01 18:00:00+00:00   
1134           1134       0  13295.123821 2025-12-02 03:00:00+00:00   
1135           1135       0  13302.569438 2025-12-02 10:00:00+00:00   
1136           1136       0  13316.829484 2025-12-02 16:00:00+00:00   
1137           1137       0  13291.008266 2025-12-02 20:00:00+00:00   
1138           1138       0  13272.753143 2025-12-03 02:00:00+00:00   
1139           1139       0  13266.015879 2025-12-03 06:00:00+00:00   
1140           1140       0  13245.685561 2025-12-03 10:00:00+00:00   
1141           1141       0  13229.033135 2025-12-03 19:00:00+00:00   
1142           1142       0  13241.578201 2025-12-04 00:00:00+00:00   
1143           1143       0  13223.480837 2025-12-04 09:00:00+00:00   
1144           1144       0  13254.036536 2025-12-04 18:00:00+00:00   
1145           1145       0  13247.602427 2025-12-05 06:00:00+00:00   
1146           1146       0  13275.192348 2025-12-05 16:00:00+00:00   
1147           1147       0  13258.344616 2025-12-08 02:00:00+00:00   
1148           1148       0  13251.272468 2025-12-08 06:00:00+00:00   
1149           1149       0  13294.120730 2025-12-08 15:00:00+00:00   

      Avg Entry Price  Entry Fees            Exit Timestamp  Avg Exit Price  \
1129          1.15704         0.0 2025-11-28 10:00:00+00:00        1.156340   
1130          1.16074         0.0 2025-12-01 10:00:00+00:00        1.162370   
1131          1.16278         0.0 2025-12-01 12:00:00+00:00        1.163060   
1132          1.16290         0.0 2025-12-01 17:00:00+00:00        1.162105   
1133          1.16120         0.0 2025-12-02 00:00:00+00:00        1.160660   
1134          1.16122         0.0 2025-12-02 04:00:00+00:00        1.160920   
1135          1.16066         0.0 2025-12-02 11:00:00+00:00        1.161070   
1136          1.15954         0.0 2025-12-02 19:00:00+00:00        1.161760   
1137          1.16246         0.0 2025-12-03 01:00:00+00:00        1.163255   
1138          1.16382         0.0 2025-12-03 05:00:00+00:00        1.164190   
1139          1.16430         0.0 2025-12-03 08:00:00+00:00        1.164390   
1140          1.16606         0.0 2025-12-03 18:00:00+00:00        1.166885   
1141          1.16728         0.0 2025-12-03 20:00:00+00:00        1.166860   
1142          1.16630         0.0 2025-12-04 03:00:00+00:00        1.165880   
1143          1.16777         0.0 2025-12-04 13:00:00+00:00        1.166560   
1144          1.16544         0.0 2025-12-04 20:00:00+00:00        1.165220   
1145          1.16594         0.0 2025-12-05 07:00:00+00:00        1.166230   
1146          1.16343         0.0 2025-12-08 00:00:00+00:00        1.165000   
1147          1.16538         0.0 2025-12-08 03:00:00+00:00        1.165120   
1148          1.16608         0.0 2025-12-08 09:00:00+00:00        1.165450   
1149          1.16251         0.0 2025-12-09 05:00:00+00:00        1.164840   

      Exit Fees        PnL    Return Direction  Status  Position Id  
1129        0.0  -9.349738 -0.000605      Long  Closed         1129  
1130        0.0 -21.698194 -0.001404     Short  Closed         1130  
1131        0.0  -3.719190 -0.000241     Short  Closed         1131  
1132        0.0 -10.557992 -0.000684      Long  Closed         1132  
1133        0.0  -7.180492 -0.000465      Long  Closed         1133  
1134        0.0   3.988537  0.000258     Short  Closed         1134  
1135        0.0   5.454053  0.000353      Long  Closed         1135  
1136        0.0  29.563361  0.001915      Long  Closed         1136  
1137        0.0 -10.566352 -0.000684     Short  Closed         1137  
1138